In [ ]:
import numpy as np

import matplotlib.pyplot as plt

from CADETProcess.processModel import ComponentSystem
from CADETProcess.processModel import NoBinding
from CADETProcess.processModel import Source, LumpedRateModelWithPores, Sink
from CADETProcess.processModel import FlowSheet
from CADETProcess.processModel import Process
from CADETProcess.simulator import Cadet
from CADETProcess.comparison import Comparator
from CADETProcess.reference import ReferenceIO
from CADETProcess.optimization import OptimizationProblem
from CADETProcess.optimization import U_NSGA3
from CADETProcess import settings



# Import Data
mydata = np.loadtxt('C:/Users/Nutzer/Desktop/CADET_Office_Hours/Y_ajayi/75cmph_1.csv', 
                    delimiter=',')
time = mydata[:, 0]*60  # Convert time data from minutes to seconds
conductivity = mydata[:,1]
concentration = ((conductivity/1000)*0.64)/58.44
# plt.plot(time,concentration)

# Set Parameters
inlet_conc = 1000  # 1M NaCl = 1000 mol m-3
feed_flowrate = 0.48  # ml/min
vol_flowrate = feed_flowrate*((1e-6)/60)  # m^3 s-1, Convert feed flow rate units
col_length = 2.5  # cm, column length
col_ID = 0.7  # cm, column inner diameter
col_csa = np.pi*(col_ID/100)**2  # m^2, column cross sectional area
particle_diameter = 5e-5  # m, MSSpCC particle diameter
sim_duration = 1200  # s, Equivalent to the load time

#### CADET-Process
component_system = ComponentSystem(1) # One component, i.e. target protein or material
binding_model = NoBinding(component_system, name='nobinding')
feed_unit = Source(component_system, name='feed')
feed_unit.c = [max(concentration)]
column = LumpedRateModelWithPores(component_system,name='column')
column.length = col_length/100 # m
column.diameter = col_ID/100 # m
column.axial_dispersion = 1e-7
column.bed_porosity = 0.4 # -
column.particle_porosity = 0.4 # -
column.particle_radius = particle_diameter/2 # m
column.film_diffusion = [0] #
column.binding_model = binding_model # Attach the configured binding model to the column
outlet = Sink(component_system, name='outlet')
flow_sheet = FlowSheet(component_system)
flow_sheet.add_unit(feed_unit)
flow_sheet.add_unit(column)
flow_sheet.add_unit(outlet)
flow_sheet.add_connection(feed_unit, column)
flow_sheet.add_connection(column, outlet)
process = Process(flow_sheet, 'process')
process.cycle_time = time[-1]
process.add_event('feed_on', 'flow_sheet.feed.flow_rate', vol_flowrate, 0)
process_simulator = Cadet()
simulation_results = process_simulator.simulate(process)
_ = simulation_results.solution.column.outlet.plot()


# Reference
reference = ReferenceIO('Exp_1', time, concentration)
reference.plot()

#Comparator
comparator = Comparator()
comparator.add_reference(reference)
comparator.add_difference_metric('Shape', reference, 'column.outlet', use_derivative=False)

metrics = comparator.evaluate(simulation_results)
print(metrics)
_ = comparator.plot_comparison(simulation_results)


#Optimzation Problem
optimization_problem = OptimizationProblem('MSSpCC')
optimization_problem.add_evaluation_object(process)
optimization_problem.add_variable('flow_sheet.column.bed_porosity', lb=0, ub=1, name='bed_poros', transform='auto')
optimization_problem.add_variable('flow_sheet.column.axial_dispersion', lb=1e-8, ub=1e-5, name='axial_dispersion', transform='auto')
optimization_problem.add_variable('flow_sheet.column.particle_porosity', lb=0, ub=1, name='particle_porsosity', transform='auto')


optimization_problem.add_evaluator(process_simulator)

optimization_problem.add_objective(comparator,n_objectives=comparator.n_metrics, requires=[process_simulator])


settings.working_directory = 'C:/Users/Nutzer/Desktop/CADET_Office_Hours/Y_ajayi/Results_Parameter_est'


def callback(
        simulation_results, individual, evaluation_object, callbacks_dir='./'):
    comparator.plot_comparison(
        simulation_results,
        file_name=f'{callbacks_dir}/{individual.id}_{evaluation_object}_comparison.png',
        show=False
    )

optimization_problem.add_callback(
    callback, requires=[process_simulator], frequency= 1, keep_progress=True
)


optimizer = U_NSGA3()
optimizer.progress_frequency = 1 
optimizer.pop_size = 2
optimizer.n_max_gen = 5
optimizer.n_cores = 1
if __name__ == '__main__':
    print('Starting optimization')
    optimization_results = optimizer.optimize(
        optimization_problem,
        use_checkpoint=True
    )  
    
    
